In [1]:
#import libraries
#ee = official Earth Engine Python API provided by Google
import ee
import folium
#Python package built on top of the ee library 
#improves ease of use- GEE data w/in Jupyter notebooks
import geemap
from IPython.display import display
import zipfile
import os
import geopandas as gpd

In [2]:
#checking libraries
!pip list
#geemap included after terminal installation in gee environment

Package                   Version
------------------------- --------------
affine                    2.4.0
aiohttp                   3.9.5
aiosignal                 1.3.1
aniso8601                 9.0.1
annotated-types           0.6.0
anyio                     4.3.0
appnope                   0.1.4
archspec                  0.2.3
argon2-cffi               23.1.0
argon2-cffi-bindings      21.2.0
arrow                     1.3.0
asttokens                 2.4.1
async-lru                 2.0.4
async-timeout             4.0.3
attrs                     23.2.0
Babel                     2.14.0
backcall                  0.2.0
beautifulsoup4            4.12.3
bleach                    6.1.0
blinker                   1.8.2
bokeh                     3.1.1
boltons                   24.0.0
bqplot                    0.12.43
branca                    0.7.2
Brotli                    1.1.0
cached-property           1.5.2
cachelib                  0.9.0
cachetools                5.3.3
certifi              

In [3]:
! python --version

Python 3.8.19


In [4]:
# Create a folium Map object
map = folium.Map(location=[20, 0], zoom_start=2)

# Display the map
display(map)

In [5]:
kern_county_coords = [35.3, -119]

# Create a folium Map object
kern_map = folium.Map(location= kern_county_coords, zoom_level=8)
                      
#Display the map
display(kern_map)

In [6]:
#changing from folium to geemap

map = geemap.Map()
map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

In [7]:
for basemap in geemap.basemaps.keys():
    print(basemap)


OpenStreetMap
Esri.WorldStreetMap
Esri.WorldImagery
Esri.WorldTopoMap
FWS NWI Wetlands
FWS NWI Wetlands Raster
NLCD 2021 CONUS Land Cover
NLCD 2019 CONUS Land Cover
NLCD 2016 CONUS Land Cover
NLCD 2013 CONUS Land Cover
NLCD 2011 CONUS Land Cover
NLCD 2008 CONUS Land Cover
NLCD 2006 CONUS Land Cover
NLCD 2004 CONUS Land Cover
NLCD 2001 CONUS Land Cover
USGS NAIP Imagery
USGS NAIP Imagery False Color
USGS NAIP Imagery NDVI
USGS Hydrography
USGS 3DEP Elevation
ESA Worldcover 2020
ESA Worldcover 2020 S2 FCC
ESA Worldcover 2020 S2 TCC
ESA Worldcover 2021
ESA Worldcover 2021 S2 FCC
ESA Worldcover 2021 S2 TCC
BaseMapDE.Color
BaseMapDE.Grey
BasemapAT.basemap
BasemapAT.grau
BasemapAT.highdpi
BasemapAT.orthofoto
BasemapAT.overlay
BasemapAT.surface
BasemapAT.terrain
CartoDB.DarkMatter
CartoDB.DarkMatterNoLabels
CartoDB.DarkMatterOnlyLabels
CartoDB.Positron
CartoDB.PositronNoLabels
CartoDB.PositronOnlyLabels
CartoDB.Voyager
CartoDB.VoyagerLabelsUnder
CartoDB.VoyagerNoLabels
CartoDB.VoyagerOnlyLabe

In [8]:
#Basemap and ROI

#centering map on Kern County
#using geemap to create a map object
kern_map = geemap.Map(center=[35.3, -119], zoom=9)

In [9]:
# Add Google Earth Engine terrain basemap
kern_map.add_basemap("Esri.WorldTerrain",labels=False) #gives a message that this has already been added

kern_map

Map(center=[35.3, -119], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(…

In [10]:
#below code doesn't work
#feature_coll = ee.data.getFeatureCollections()

#from Mistral
#there isn't a built-in function to get a list of all feature collections in the Earth Engine API. 
#However, you can still access individual feature collections if you know their IDs.
#For example, here's how you can load the "Global Forest Change" feature collection:

# Load the Global Forest Change feature collection.
gfc = ee.FeatureCollection('UMD/hansen/global_forest_change_2018_v1_6')

# Print the first feature in the collection.
print(gfc.first())


ee.Element({
  "functionInvocationValue": {
    "functionName": "Collection.first",
    "arguments": {
      "collection": {
        "functionInvocationValue": {
          "functionName": "Collection.loadTable",
          "arguments": {
            "tableId": {
              "constantValue": "UMD/hansen/global_forest_change_2018_v1_6"
            }
          }
        }
      }
    }
  }
})


In [12]:
#Creating the county boundaries

# Load the California counties feature collection
counties = ee.FeatureCollection("TIGER/2018/Counties")

# Filter the feature collection to get only California counties
ca_counties = counties.filter(ee.Filter.eq('STATEFP', '06'))

palette = ["FFFFFF"]

# Define the style parameters for the county boundaries
vis_params = {
   "color": "666666",
    "colorOpacity": .4,
    "pointSize": 3,
    "pointShape": "circle",
    "width": 2,
    "lineType": "solid",
    "fillColorOpacity": 0.07,
}
# Add the California counties feature collection to the map with the custom visualization parameter
kern_map.add_styled_vector(ca_counties, column="NAME", palette = palette, layer_name = 'California Counties', **vis_params,)

In [13]:
kern_map

Map(bottom=207499.0, center=[35.26400862844068, -118.30696105957033], controls=(WidgetControl(options=['positi…

In [16]:
#converts the filtered feature colleciton to a list
county_list = ca_counties.getInfo()['features']

In [15]:
county_list

[{'type': 'Feature',
  'geometry': {'type': 'Polygon',
   'coordinates': [[[-122.6464143966072, 38.598596111178],
     [-122.64632463444183, 38.598192117071285],
     [-122.64596558499663, 38.59810238759981],
     [-122.64574113534296, 38.59805749311838],
     [-122.64506786967013, 38.597788187200976],
     [-122.64488834290992, 38.597518903786096],
     [-122.64434976074871, 38.59653146236425],
     [-122.64390094012617, 38.59563376768178],
     [-122.6435867214103, 38.59491564141987],
     [-122.64210563804826, 38.593883330696855],
     [-122.64129774188908, 38.59271634737013],
     [-122.64098351522001, 38.59181871002553],
     [-122.64053467990746, 38.591100570318076],
     [-122.63954723532652, 38.59002335636946],
     [-122.6390086251966, 38.5896642886085],
     [-122.63815586317442, 38.589260367943965],
     [-122.63743770599612, 38.588317840681185],
     [-122.63667470161968, 38.587554833606056],
     [-122.63604639155315, 38.587195734083174],
     [-122.63564237735798, 38.5869

In [17]:
# Convert the filtered FeatureCollection to a gdf
#just an exercise to view columns
county_gdf = gpd.GeoDataFrame.from_features(county_list)

# Display the gdf
print(county_gdf.head())


kern_county = ca_counties.filter(ee.Filter.eq('STATEFP', '06')) \
                         .filter(ee.Filter.eq('NAME', 'Kern'))
kern_county

                                            geometry       ALAND     AWATER  \
0  POLYGON ((-122.64641 38.59860, -122.64632 38.5...  1938114186  104300794   
1  POLYGON ((-123.13452 38.29626, -123.12613 38.2...  1347976788  797029137   
2  GEOMETRYCOLLECTION (LINESTRING (-122.25544 37....  1857233047  225282636   
3  POLYGON ((-122.58816 37.57939, -122.58789 37.5...  1161960635  757110545   
4  GEOMETRYCOLLECTION (LINESTRING (-122.25521 37....  1909598013  216923745   

  CBSAFP CLASSFP COUNTYFP  COUNTYNS CSAFP FUNCSTAT  GEOID     INTPTLAT  \
0  34900      H1      055  00277292   488        A  06055  +38.5070999   
1  41860      H1      041  00277285   488        A  06041  +38.0518169   
2  41860      H1      013  01675903   488        A  06013  +37.9194790   
3  41860      H1      081  00277305   488        A  06081  +37.4146725   
4  41860      H1      001  01675839   488        A  06001  +37.6471385   

       INTPTLON LSAD METDIVFP  MTFCC          NAME             NAMELSAD  \
0  -1

In [24]:
#use this next
#https://github.com/gee-community/geemap/blob/master/examples/notebooks/geopandas.ipynb

In [25]:
#!pip install googledrivedownloader

In [26]:
#!pip install pygis

In [18]:
#define shapefile location
url = "https://drive.google.com/file/d/1mjXFF1HMfkGGWL_0-cZMNgyrCSPRRtmj/view?usp=share_link"

#define output location
out_file = '/Users/jenniferbadger/Documents/GitHub/GEE_AI_Course/kern_almonds_dissolve.zip'

#this pulls a file from a url and puts it 
#in a defined location
geemap.download_file(url, out_file)

/Users/jenniferbadger/Documents/GitHub/GEE_AI_Course/kern_almonds_dissolve.zip already exists. Skip downloading. Set overwrite=True to overwrite.


'/Users/jenniferbadger/Documents/GitHub/GEE_AI_Course/kern_almonds_dissolve.zip'

In [19]:
#importing shp
in_shp = "/Users/jenniferbadger/Documents/GitHub/GEE_AI_Course/kern_almond_dissolve/kern2019_almonds_dissolve_.shp"

#defining visual parameters
almond_params = {
    'color': '#b3e2cd',  # Stroke color
    'weight': 1,          # Stroke weight
    'opacity': 0.8,       # Stroke opacity (0 to 1)
    'fillColor': 'grey', # Fill color
    'fillOpacity': 0.1   # Fill opacity (0 to 1)
}

#wihtout this function, the shp gets continually added to the basemap
if "Almonds" not in map.layers:
    kern_map.add_shp(in_shp, layer_name="Almonds", style=almond_params)

kern_map

Map(bottom=52103.0, center=[35.25683378961826, -119.01763916015625], controls=(WidgetControl(options=['positio…

In [68]:
# Load your ImageCollection
image_collection = ee.ImageCollection('NASA/GDDP-CMIP6') \
    .filter(ee.Filter.eq('model', 'CESM2')) \
    .filter(ee.Filter.eq('scenario', 'ssp245'))

# Aggregate the start dates of all images in the collection
start_dates = image_collection.aggregate_array('system:time_start')

# Find the minimum and maximum start dates
min_start_date = ee.Date(ee.Number(start_dates.reduce(ee.Reducer.min())))
max_start_date = ee.Date(ee.Number(start_dates.reduce(ee.Reducer.max())))

# Get the min and max start dates in a human-readable format
min_start_date_str = min_start_date.format('YYYY-MM-dd').getInfo()
max_start_date_str = max_start_date.format('YYYY-MM-dd').getInfo()

# Print the start and end dates
print('Start date:', min_start_date_str)
print('End date:', max_start_date_str)

Start date: 2015-01-01
End date: 2100-12-31


In [21]:
#example of date params as variable
#but didn't use it
#returns an image collection 
#with 365 elements - 
#one for each day in 2020
start_date = '2020-01-01'
end_date = '2020-12-31'

# Load the NASA GDDP CMIP6 dataset
#if I use start_date/end_date, then I get 365 elements
#instead using one date: August 1st, 2100
#model = CESM2
#scenario 245
#As an update to scenario RCP4.5, SSP245 with an additional radiative forcing of 4.5 W/m² by the year 2100 
#represents the medium pathway of future greenhouse gas emissions. 
#This scenario assumes that climate protection measures are being taken.
cmip6 = ee.ImageCollection('NASA/GDDP-CMIP6') \
    .filterDate('2100-08-01', '2100-08-02') \
    .filter(ee.Filter.eq('model', 'CESM2')) \
    .filter(ee.Filter.eq('scenario', 'ssp245')) \

In [22]:
cmip6 #contains 7 bands, including hurs, tas, etc.

In [23]:
# Select the temperature at surface band
#to see the metadata
tas = cmip6.select('tas')

tas #contains only the tas band

In [30]:
#From GEE - ReduceRegion
#ee.Image.reduceRegion
#Applies a reducer to all the pixels in a specific region.

#Using this example to get Kern stats...
#A Landsat 8 surface reflectance image with SWIR1, NIR, and green bands.
#From https://www.usgs.gov/faqs/what-are-best-landsat-spectral-bands-use-my-research
#band 3 - green; Emphasizes peak vegetation, which is useful for assessing plant vigor
#band 5 near infrared, Emphasizes biomass content and shorelines
#band 6 - short wave infrared; discriminates moisture content of soil and vegetation; penetrates thin clouds
img = ee.Image('LANDSAT/LC08/C02/T1_L2/LC08_044034_20210508').select(
    ['SR_B6', 'SR_B5', 'SR_B3']
)

# Santa Cruz Mountains ecoregion geometry.
geom = (
    ee.FeatureCollection('EPA/Ecoregions/2013/L4')
    .filter('us_l4name == "Santa Cruz Mountains"')
    .geometry()
)

# Display layers on the map.
m = geemap.Map()
m.set_center(-122.08, 37.22, 8.5)
m.add_layer(img, {'min': 10000, 'max': 20000}, 'Landsat image')
#this is the vector of Santa Cruz Mtns
m.add_layer(geom, {'color': 'white'}, 'Santa Cruz Mountains ecoregion')
display(m)


Map(center=[37.22, -122.08], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchData…

In [29]:
# Calculate median band values within Santa Cruz Mountains ecoregion. It is
# good practice to explicitly define "scale" (or "crsTransform") and "crs"
# parameters of the analysis to avoid unexpected results from undesired
# defaults when e.g. reducing a composite image.
stats = img.reduceRegion(
    reducer=ee.Reducer.median(),
    geometry=geom,
    scale=30, # meters
    crs='EPSG:3310',  # California Albers projection
)

stats

# A dictionary is returned: keys are band names, values are the statistic.
display('Median band values, Santa Cruz Mountains ecoregion', stats)


'Median band values, Santa Cruz Mountains ecoregion'

In [32]:
#You can combine reducers to calculate mean and standard deviation simultaneously
#The output dictionary keys are the concatenation of the band names and statistic names
reducer = ee.Reducer.mean().combine(
    reducer2=ee.Reducer.stdDev(), sharedInputs=True
)
multi_stats = img.reduceRegion(
    reducer=reducer,
    geometry=geom,
    scale=30,
    crs='EPSG:3310',
)
display('Mean & SD band values, Santa Cruz Mountains ecoregion', multi_stats)

'Mean & SD band values, Santa Cruz Mountains ecoregion'

In [41]:
# Select the first (and only) image from the image collection
single_image = cmip6.first()

# Select the tas air temperature band
#redefining above variable tas
tas = single_image.select('tas')

# Reduce the single image to compute the minimum and maximum temperatures for the entire region
#reduceRegion() method computes min + max temps for each image in the collection. 
#The minMax() reducer computes both the minimum and maximum values.
min_max = tas.reduceRegion(
    reducer=ee.Reducer.minMax(),
    geometry=kern_county,
    scale=1000,  # Adjust the scale as needed
    crs='EPSG:3310' # California Albers projection
)

In [42]:
min_max

In [43]:
# Extract the minimum and maximum temperatures from the result
min_temp = min_max.get('tas_min')
max_temp = min_max.get('tas_max')

# Print the min and max temperatures
print('Minimum temperature:', min_temp.getInfo()) #290.882
print('Maximum temperature:', max_temp.getInfo()) #302.114

Minimum temperature: 290.8829650878906
Maximum temperature: 302.1143493652344


In [44]:
# Clip the raster band to the polygon geometry
tas_clipped = tas.clip(kern_county)

# Convert Kelvin to Fahrenheit
tas_fahrenheit = tas_clipped.multiply(9/5).subtract(459.67)

# Print the clipped and converted raster band
print('Clipped and converted max temperature:', tas_fahrenheit.getInfo())


Clipped and converted max temperature: {'type': 'Image', 'bands': [{'id': 'tas', 'data_type': {'type': 'PixelType', 'precision': 'double'}, 'crs': 'EPSG:4326', 'crs_transform': [0.25, 0, -180, 0, -0.25, 90]}]}


In [62]:
min_maxF = tas_fahrenheit.reduceRegion(
    reducer=ee.Reducer.minMax(),
    geometry=kern_county,
    scale=1000,  # Adjust the scale as needed
    crs='EPSG:3310' # California Albers projection
)

min_maxF

In [45]:
# Access the 'tas' band from the Image object
tas_band = tas_fahrenheit.select('tas')

# Print information about the 'tas' band
print('Information about the tas band:', tas_band.getInfo())

Information about the tas band: {'type': 'Image', 'bands': [{'id': 'tas', 'data_type': {'type': 'PixelType', 'precision': 'double'}, 'crs': 'EPSG:4326', 'crs_transform': [0.25, 0, -180, 0, -0.25, 90]}]}


In [46]:
# Get the pixel values of the 'tas' band
tas_values = tas_band.reduceRegion(
    reducer=ee.Reducer.toList(),
    geometry=kern_county,
    scale=1000  # Adjust the scale as needed
).get('tas').getInfo()

# Print the list of tas values
print('List of tas values:', tas_values)

List of tas values: [68.00295532226568, 68.00295532226568, 68.00295532226568, 68.00295532226568, 68.00295532226568, 68.00295532226568, 68.00295532226568, 68.00295532226568, 68.00295532226568, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 69.57943847656253, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 79.57194335937498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.51432617187498, 81.5143261

In [51]:
# Get the maximum temperature
max_tas = max(tas_values)

# Get the minimum temperature
min_tas = min(tas_values)

# Print the maximum and minimum temperatures
print('Maximum temperature:', max_tas)
print('Minimum temperature:', min_tas)

Maximum temperature: 84.13582885742193
Minimum temperature: 63.91933715820318


In [52]:
tas #is an image

In [57]:
tas_stats = tas.reduceRegion(ee.Reducer.minMax(), kern_county, scale=1000).getInfo()

min_tas = tas_stats['tas_min']
max_tas = tas_stats['tas_max']

tas_vis_params = {
    'bands': ['tas'],
    'min': min_tas,
    'max': max_tas,
    'palette': ['#FFFFB2', '#FFCC66','#FF8C00','#FF4500','#D70000'],
   'opacity': 0.4  # Add opacity parameter here
}

#'palette': ['#FFFFB2', '#FFE082', '#FFCC66', '#FFB14C', '#FF8C00', '#FF6100', '#FF4500', '#FF2400', '#D70000']

if "TAS" not in map.layers:
    kern_map.addLayer(tas.clip(kern_county), tas_vis_params, "TAS")

# Display the map
kern_map

#interact is used to adjust properties of a map layer dynamically.
#This tuple represents the range and step size for an opacity slider control.
#opacity_slider = kern_map.layers[-1].interact(opacity=(0.0, 1.0, 0.1))

# Ensure the layer control is active to adjust opacity among other settings
#kern_map.addLayerControl(0.9)

Map(bottom=52084.0, center=[35.3, -119], controls=(WidgetControl(options=['position', 'transparent_bg'], widge…

In [55]:
#helpful snippets

#map.clear_layers()
#map.addLayer(image, vis_params, "Layer Name")

#in geemap, you can't rearrange the layer 'z' order
#you must remove layers and then add them back
#in the desired order

# Remove all layers
#kern_map.layers = []

kern_map = geemap.Map(center=[35.3, -119], zoom=9)

if "Esri.WorldTerrain" not in map.layers:
    kern_map.add_basemap("Esri.WorldTerrain",labels=False) 

if "TAS" not in map.layers:
    kern_map.addLayer(tas.clip(kern_county), tas_vis_params, "TAS")

if "Almonds" not in map.layers:
     kern_map.add_shp(in_shp, layer_name="Almonds", style=almond_params)
    
if 'California Counties' not in map.layers:
     kern_map.add_styled_vector(ca_counties, column="NAME", palette = palette, layer_name = 'California Counties', **vis_params,)

# Display the map
kern_map

Map(center=[35.3, -119], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(…

In [59]:
#have to remove legends
#or will be repeated
kern_map.remove_legends()

#picked these out from the larger palette 
#'#FF6100', '#FF4500', '#FF2400', '#D70000'

# Define legend parameters
legend_dict = {
    '0 - 25°F': '#FFFFB2',
    '25 - 50°F': '#FFCC66',
    '50 - 75°F': '#FF8C00',
    '75 - 100°F': '#FF4500',
    '100 - 125°F': '#D70000'
}

# Add legend to the map
kern_map.add_legend(title="TAS (°F)", legend_dict=legend_dict)

kern_map

Map(bottom=52318.0, center=[34.773203753940734, -118.74572753906251], controls=(WidgetControl(options=['positi…

In [65]:
kern_map.remove_legends()

tas_statsF = tas_fahrenheit.reduceRegion(ee.Reducer.minMax(), kern_county, scale=1000).getInfo()

min_tasF = tas_statsF['tas_min']
max_tasF = tas_statsF['tas_max']

tas_vis_paramsF = {
    'bands': ['tas_fahrenheit'],
    'min': min_tasF,
    'max': max_tasF,
    'palette': ['#FFFFB2', '#FFCC66','#FF8C00','#FF4500','#D70000'],
   'opacity': 0.4  # Add opacity parameter here
}

#kern_map.add_controls() for continuous legend
kern_map.add_colorbar(tas_vis_paramsF, label="Temp at Surface (F)", layer_name="TAS", orientation="vertical")
kern_map

Map(bottom=52092.0, center=[35.28150065789119, -118.84735107421875], controls=(WidgetControl(options=['positio…